## 1. Import the packages needed

In [1]:
import pandas as pd
import numpy as np
from itertools import product
from math import sqrt
import gurobipy as gp
from gurobipy import GRB
import os
from IPython.display import clear_output

## 2. Read the datasets

In [2]:
grid_population = pd.read_csv("munich_population.csv")

In [3]:
grid_population

Longitude   Latitude  population  distance-Candidplatz  \
0      11.500833  48.245000   13.032483             15.668726   
1      11.507937  48.245000   19.297748             15.499806   
2      11.501667  48.244167   12.316271             15.560698   
3      11.502913  48.244167   23.806235             15.530048   
4      11.505833  48.243790   19.737550             15.420449   
...          ...        ...         ...                   ...   
10955  11.513076  48.065288   54.855114              6.790137   
10956  11.514528  48.065472   95.249631              6.705640   
10957  11.516252  48.065542   82.435340              6.619121   
10958  11.512942  48.064167   36.104766              6.892781   
10959  11.514612  48.063751   53.004641              6.851224   

       distance-Fraunhoferstraße  distance-Georg-Brauchle-Ring  distance-Gern  \
0                      13.994687                      8.063432       9.382074   
1                      13.796666                      7.941917       9.277821   
2                      13.885205                      7.957894       9.277960   
3                      13.849338                      7.934600       9.257983   
4                      13.728510                      7.843167       9.173524   
...                          ...                           ...            ...   
10955                   8.446503                     12.257802      10.906099   
10956                   8.371217                     12.227396      10.874460   
10957                   8.296797                     12.208826      10.854552   
10958                   8.557010                     12.382908      11.031169   
10959                   8.530487                     12.417450      11.064251   

       distance-Hauptbahnhof  distance-Kolumbusplatz  distance-Laurinplatz  \
0                  12.477091               15.020498             17.738960   
1                  12.297270               14.830991             17.600421   
2                  12.368396               14.911417             17.632831   
3                  12.335577               14.877117             17.607627   
4                  12.221648               14.759581             17.509897   
...                      ...                     ...                   ...   
10955               9.073297                7.673158              4.954584   
10956               9.012387                7.590952              4.855567   
10957               8.956485                7.507406              4.748623   
10958               9.191951                7.778003              5.037376   
10959               9.186950                7.740208              4.967874   

       ...  distance-locker-323  distance-locker-324  distance-locker-325  \
0      ...            13.400702             6.908782            10.752613   
1      ...            13.163933             6.731251            10.418831   
2      ...            13.289899             6.799825            10.641928   
3      ...            13.247212             6.766371            10.582132   
4      ...            13.111747             6.652798            10.411492   
...    ...                  ...                  ...                  ...   
10955  ...             9.699457            13.664758            13.248417   
10956  ...             9.623453            13.631861            13.181151   
10957  ...             9.547936            13.610157            13.116715   
10958  ...             9.809449            13.789779            13.364018   
10959  ...             9.781614            13.821306            13.349450   

       distance-locker-326  distance-locker-327  distance-locker-328  \
0                 9.481736             9.242825             7.869698   
1                 9.666314             9.398974             8.051292   
2                 9.414671             9.170693             7.801705   
3                 9.446029             9.196936             7.832316   
4                 9.483556     

In [4]:
Lockers = pd.read_csv("locker_locations.csv", sep =",", encoding="UTF-8")

In [5]:
Lockers

Type                  Street  Postal Code Province  \
0                   DHL        Bodenseestr. 253        81249  München   
1    Amazon Hub Locker          BODENSEESTR. 40        81243  München   
2    Amazon Hub Locker         Brunhamstraße 21        81249  München   
3    Amazon Hub Locker            Cosimastr. 10        81927  München   
4    Amazon Hub Locker         Freischützstr. 4        81927  München   
..                  ...                     ...          ...      ...   
178                 DHL     Winterthurer Str. 2        81476  München   
179                 DHL  Wolfratshauser Str. 76        81379  München   
180                 DHL            Wotanstr. 85        80639  München   
181                 DHL        Zielstattstr. 63        81379  München   
182                 DHL         Zschokkestr. 32        80687  München   

             Source   Latitude  Longitude        Name  
0    amazon website  48.142240  11.423161  locker-296  
1    amazon website  48.146895  11.451456  locker-297  
2    amazon website  48.140608  11.426319  locker-298  
3    amazon website  48.155712  11.630130  locker-299  
4    amazon website  48.157533  11.642324  locker-301  
..              ...        ...        ...         ...  
178     dhl website  48.095632  11.496505  locker-291  
179     dhl website  48.094330  11.540310  locker-292  
180     dhl website  48.152772  11.507182  locker-293  
181     dhl website  48.102050  11.527656  locker-294  
182     dhl website  48.135292  11.520055  locker-295  

[183 rows x 8 columns]

In [6]:
ubahn_stations = pd.read_excel("ubahn_stations.xlsx")

In [7]:
ubahn_stations = ubahn_stations.drop_duplicates(["Name","District"]).reset_index().iloc[:,1:]

In [8]:
ubahn_stations

Type                 Name                      District   Latitude  \
0    U-Bahn          Candidplatz       Untergiesing-Harlaching  48.112222   
1    U-Bahn     Fraunhoferstraße  Ludwigsvorstadt-Isarvorstadt  48.129167   
2    U-Bahn  Georg-Brauchle-Ring                       Moosach  48.175000   
3    U-Bahn                 Gern         Neuhausen-Nymphenburg  48.162778   
4    U-Bahn         Hauptbahnhof  Ludwigsvorstadt-Isarvorstadt  48.140278   
..      ...                  ...                           ...        ...   
98   U-Bahn          Martinsried                           NaN  48.109167   
99   U-Bahn         Nordfriedhof            Schwabing-Freimann  48.173056   
100  U-Bahn        Partnachplatz             Sendling-Westpark  48.116944   
101  U-Bahn       Studentenstadt            Schwabing-Freimann  48.183611   
102  U-Bahn             Westpark             Sendling-Westpark  48.118056   

     Longitude  
0    11.571389  
1    11.574444  
2    11.529167  
3    11.529167  
4    11.561111  
..         ...  
98   11.451667  
99   11.596944  
100  11.526667  
101  11.607778  
102  11.516111  

[103 rows x 5 columns]

### The locker and U-Bahn datasets are merged in one dataframe named 'stations'.

In [9]:
stations = Lockers.iloc[:,[0,-1,-3,-2]].append(ubahn_stations.iloc[:,[0,1,3,4]], ignore_index=True)

In [10]:
stations

Type            Name   Latitude  Longitude
0                   DHL      locker-296  48.142240  11.423161
1    Amazon Hub Locker       locker-297  48.146895  11.451456
2    Amazon Hub Locker       locker-298  48.140608  11.426319
3    Amazon Hub Locker       locker-299  48.155712  11.630130
4    Amazon Hub Locker       locker-301  48.157533  11.642324
..                  ...             ...        ...        ...
281              U-Bahn     Martinsried  48.109167  11.451667
282              U-Bahn    Nordfriedhof  48.173056  11.596944
283              U-Bahn   Partnachplatz  48.116944  11.526667
284              U-Bahn  Studentenstadt  48.183611  11.607778
285              U-Bahn        Westpark  48.118056  11.516111

[286 rows x 4 columns]

## 3. Optimization Model Definition

#### First, the indexes are defined.

In [11]:
customers = grid_population.index
facilities = stations.index
lockers = Lockers.index
population = grid_population.population
cartesian_prod = list(product(range(len(customers)), range(len(facilities))))

#### Value add per parcel function is defined. Taking the distance as an argument.

In [12]:
def will2p(distance,x):
    if distance<=0.200:
        w2p = x
    elif distance<=3.000:
        w2p = x*(3.000-distance)/2.800
    else:
        w2p = 0
    return w2p

#### Values to be used in sensitivity analysis are defined.

In [13]:
list_demand_rate = [0.5, 1.5, 3.0, 4.5]
list_vappc = [0.25,0.50,1.00,1.50, 2.00, 3.00]
list_opc_locker = [5000,10000,12500,15000,20000]
list_capacitypa = [8000,10000,12500,15000,20000]

#### Model is defined with for loops outside to run all combinations for a sensitvity analysis.

In [ ]:
counter = 0
for vappc in list_vappc:
    will2pay = {(c,f): will2p(grid_population["distance-"+stations["Name"].iloc[f]].iloc[c],vappc) for c, f in cartesian_prod}
    for demand_rate in list_demand_rate:
        for opc_locker in list_opc_locker:
            for capacity in list_capacitypa:
                counter+=1
                if((vappc*capacity)>=opc_locker):
                    m = gp.Model('facility_location')
                    m.setParam('TimeLimit', 3*60)
                    x,y = {},{}
                    for j in facilities:
                        y[j] = m.addVar(vtype=GRB.BINARY, name="y(%s)"%j)
                        for i in customers:
                            x[i,j] = m.addVar(vtype=GRB.INTEGER, name="x(%s,%s)"%(i,j))
                    demand = {(c): population.iloc[c]*demand_rate for c in customers}
                    for j in facilities:
                        if j<len(lockers):
                            if (Lockers.iloc[j,0] == "DHL"):
                                m.addConstr(gp.quicksum(x[i,j] for i in customers) <= 1200*y[j], "Capacity(%s)"%i)
                            else:
                                m.addConstr(gp.quicksum(x[i,j] for i in customers) <= 5000*y[j], "Capacity(%s)"%i)
                        else:
                            m.addConstr(gp.quicksum(x[i,j] for i in customers) <= capacity*y[j], "Capacity(%s)"%i)
                    for i in customers:
                        m.addConstr(gp.quicksum(x[i,j] for j in facilities) <= demand[i])
                    m.setObjective(
                        gp.quicksum((-1)*(stations.iloc[j,0]=="U-Bahn")*opc_locker*y[j] for j in facilities) +
                        gp.quicksum(will2pay[i,j]*x[i,j] for i in customers for j in facilities),
                        GRB.MAXIMIZE)
                    m.optimize()
                    objective_value_swm = 0
                    for j in facilities:
                        if j>=len(lockers):
                            for i in customers:
                                objective_value_swm += will2pay[i,j]*x[i,j].x
                    n_facilities = 0
                    for j in facilities:
                        n_facilities += y[j].x
                    for j in lockers:
                        n_facilities -= y[j].x
                    objective_value_swm = objective_value_swm - n_facilities*opc_locker
                    for j in facilities:
                        if j>=len(lockers):
                            tott = 0
                            for i in customers:
                                tott += will2pay[i,j]*x[i,j].x
                            if tott!=0:
                                new_row = {"scenario":counter,"demand_rate":demand_rate, "vappc":vappc,"opc_locker":opc_locker,"capacity":capacity,'indexl':j, 'revenue':tott}
                                df_marks = df_marks.append(new_row, ignore_index=True)
                    new_row = {"scenario":counter,"demand_rate":demand_rate, "vappc":vappc,"opc_locker":opc_locker,"capacity":capacity,'indexl':-1, 'revenue':objective_value_swm}
                    df_marks = df_marks.append(new_row, ignore_index=True)
                else:
                    new_row = {"scenario":counter,"demand_rate":demand_rate, "vappc":vappc,"opc_locker":opc_locker,"capacity":capacity,'indexl':-1, 'revenue':0}
                    df_marks = df_marks.append(new_row, ignore_index=True)
                if (counter%20==0):
                    df_marks.to_csv("sensitivity_analysis.csv", encoding ="UTF-8", index = False)
                clear_output(wait=True)
                print(str(counter)+" out of "+str(len(list_demand_rate)*len(list_vappc)*len(list_opc_locker)*len(list_capacitypa)))


333 out of 600
Set parameter TimeLimit to value 180


## 4. Results Data

In [26]:
df_marks.to_csv("sensitivity_analysis.csv", encoding ="UTF-8", index = False)

In [104]:
df_marks.groupby(['Name'])['Name'].count().sort_values(ascending=False).head(10).index[1:].to_list()

['Hauptbahnhof',
 'Heimeranplatz',
 'Westendstraße',
 'Kolumbusplatz',
 'Innsbrucker Ring',
 'Schwanthalerhöhe',
 'Max-Weber-Platz',
 'Olympia-Einkaufszentrum',
 'Sendlinger Tor']

In [214]:
profitable_stations = df_marks[df_marks.indexl!=-1].groupby(['indexl'])["profit"].sum().reset_index().sort_values(ascending=False,by="profit").reset_index(drop=True).merge(df_marks_v3 ,how="left", on="indexl")

In [215]:
profitable_stations = profitable_stations.sort_values(ascending=False,by="scenario").reset_index(drop=True)

In [204]:
profitable_stations.to_csv("profitable_stations.csv", encoding ="UTF-8", index = False)

In [224]:
profitable_stations

indexl   profit  scenario    Type                  Name   Latitude  \
0      238  3585911       242  U-Bahn           Odeonsplatz  48.146111   
1      275  3522265       242  U-Bahn            Großhadern  48.114722   
2      266  3485760       242  U-Bahn  Therese-Giehse-Allee  48.094444   
3      263  3564793       242  U-Bahn            Ostbahnhof  48.139167   
4      193  3545021       241  U-Bahn         Rotkreuzplatz  48.152778   
..     ...      ...       ...     ...                   ...        ...   
94     203  1896990       134  U-Bahn      Frankfurter Ring  48.187222   
95     194  1838494       128  U-Bahn        Sendlinger Tor  48.133333   
96     229  1820988       125  U-Bahn           Goetheplatz  48.129722   
97     281  1776656       123  U-Bahn           Martinsried  48.109167   
98     280   742218        97  U-Bahn   Klinikum Großhadern  48.108889   

    Longitude  
0   11.579167  
1   11.477222  
2   11.642778  
3   11.606944  
4   11.534167  
..        ...  
94  11.572778  
95  11.566667  
96  11.558889  
97  11.451667  
98  11.473889  

[99 rows x 7 columns]

In [220]:
final_results = pd.DataFrame()

In [222]:
final_results[["U-Bahn Station Name","Number of Scenarios", "Profit (€)"]] = profitable_stations[["Name","scenario", "profit"]]

In [223]:
final_results

U-Bahn Station Name  Number of Scenarios  Profit (€)
0            Odeonsplatz                  242     3585911
1             Großhadern                  242     3522265
2   Therese-Giehse-Allee                  242     3485760
3             Ostbahnhof                  242     3564793
4          Rotkreuzplatz                  241     3545021
..                   ...                  ...         ...
94      Frankfurter Ring                  134     1896990
95        Sendlinger Tor                  128     1838494
96           Goetheplatz                  125     1820988
97           Martinsried                  123     1776656
98   Klinikum Großhadern                   97      742218

[99 rows x 3 columns]

## 5. Mapping the Stations

In [225]:
import folium
from folium.plugins import HeatMap
from shapely.geometry import Point, Polygon
import geopandas as gpd

In [228]:
m_ = folium.Map([48.16,11.57], zoom_start=12, control_scale=True, tiles='cartodbpositron')


In [229]:
m_ = folium.Map([48.16,11.57], zoom_start=12, control_scale=True, tiles='cartodbpositron')
#source(choropleth): https://towardsdatascience.com/using-folium-to-generate-choropleth-map-with-customised-tooltips-12e4cec42af2
heatmap_population = HeatMap(
    data = grid_population[(grid_population.Province != "")][["Latitude", "Longitude","population"]],
    blur = 60,
    radius = 45).add_to(m_)

In [230]:
m_

### Population is shown with heatmap.

In [231]:
for i in Lockers.index:
    folium.CircleMarker(
    location = Lockers.iloc[i,[-3,-2]].to_list(),
    popup = Lockers.iloc[i,0]+" - "+ Lockers.iloc[i,1],
    color = "Red",
    fill=False,
    opacity=1,
    fillOpacity=1,
    radius=4
    ).add_to(m_)
for i in Lockers.index:
    folium.CircleMarker(
    location = Lockers.iloc[i,[-3,-2]].to_list(),
    popup = Lockers.iloc[i,0]+" - "+ Lockers.iloc[i,1],
    color = "Pink",
    fill=True,
    opacity=1,
    fillOpacity=1,
    radius=3
    ).add_to(m_)
for i in Lockers.index:
    folium.CircleMarker(
    location = Lockers.iloc[i,[-3,-2]].to_list(),
    popup = Lockers.iloc[i,0]+" - "+ Lockers.iloc[i,1],
    color = "Pink",
    fill=True,
    opacity=1,
    fillOpacity=1,
    radius=1
    ).add_to(m_)
m_

### Parcel locker locations are shown in pink.

In [233]:
for i in ubahn_stations.index:
    folium.CircleMarker(
    location = ubahn_stations.iloc[i,[-2,-1]].to_list(),
    popup = ubahn_stations.iloc[i,1],
    color = "Black",
    fill=False,
    opacity=1,
    fillOpacity=1,
    radius=7
    ).add_to(m_)
for i in ubahn_stations.index:
    folium.CircleMarker(
    location = ubahn_stations.iloc[i,[-2,-1]].to_list(),
    popup = ubahn_stations.iloc[i,1],
    color = "White",
    fill=True,
    opacity=1,
    fillOpacity=1,
    radius=4
    ).add_to(m_)
for i in ubahn_stations.index:
    folium.CircleMarker(
    location = ubahn_stations.iloc[i,[-2,-1]].to_list(),
    popup = ubahn_stations.iloc[i,1],
    color = "White",
    fill=True,
    opacity=1,
    fillOpacity=1,
    radius=1
    ).add_to(m_)

In [234]:
m_

### U-Bahn stations are shown in white.

In [239]:
selected_stations = stations[stations.index.isin(profitable_stations.indexl.to_list()[:5])].reset_index(drop=True)

In [90]:
selected_stations = stations[stations.index.isin(stations_i[:5])].reset_index(drop=True)

In [ ]:
selected_stations = selected_stations[selected_stations.Type == "U-Bahn"].reset_index(drop=True)

In [61]:
selected_stations

Type             Name   Latitude  Longitude
0  U-Bahn    Rotkreuzplatz  48.152778  11.534167
1  U-Bahn          Moosach  48.180278  11.507222
2  U-Bahn  Böhmerwaldplatz  48.143200  11.615100
3  U-Bahn           Harras  48.116667  11.536667

In [240]:
for i in selected_stations.index:
    folium.CircleMarker(
    location = selected_stations.iloc[i,[2,3]].to_list(),
    popup = selected_stations.iloc[i,1],
    color = "Black",
    fill=False,
    opacity=1,
    fillOpacity=1,
    radius=7
    ).add_to(m_)
for i in selected_stations.index:
    folium.CircleMarker(
    location = selected_stations.iloc[i,[2,3]].to_list(),
    popup = selected_stations.iloc[i,1],
    color = "Green",
    fill=True,
    opacity=1,
    fillOpacity=1,
    radius=4
    ).add_to(m_)
for i in selected_stations.index:
    folium.CircleMarker(
    location = selected_stations.iloc[i,[2,3]].to_list(),
    popup = selected_stations.iloc[i,1],
    color = "Green",
    fill=True,
    opacity=1,
    fillOpacity=1,
    radius=1
    ).add_to(m_)

In [241]:
m_

### Selected stations are shown in green.

### The map is saved in an html file.

In [242]:
m_.save("ubahn_stations.html")